<a href="https://colab.research.google.com/github/abuwildanm/Evolutionary-Algorithm/blob/master/GA_Project_(MLP).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Optimization of Multi Layer Perceptron Weight & Bias with Genetic Algorithm for Breast Cancer Classification
---

@Author : Abu Wildan Mucholladin

## Import Libraries and Tools

In [58]:
# Import standard library
import numpy as np
import pandas as pd

# Import sklearn
from sklearn.datasets import load_breast_cancer
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.preprocessing import MinMaxScaler, StandardScaler, PowerTransformer
from sklearn.decomposition import PCA
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report, precision_score, recall_score

# Import visualization library
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style('whitegrid')
%matplotlib inline
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import cufflinks as cf
cf.go_offline()

import IPython
# Plotly Configuration
# Ref : https://stackoverflow.com/questions/47230817/plotly-notebook-mode-with-google-colaboratory
def configure_plotly_browser_state():
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              plotly: 'https://cdn.plot.ly/plotly-latest.min.js?noext',
            },
          });
        </script>
        '''))
IPython.get_ipython().events.register('pre_run_cell', configure_plotly_browser_state)

In [2]:
names = ['Sample code number', 'Clump Thickness', 'Uniformity of Cell Size', 'Uniformity of Cell Shape', 'Marginal Adhesion', 'Single Epithelial Cell Size', 'Bare Nuclei', 'Bland Chromatin', 'Normal Nucleoli', 'Mitoses', 'Class']
df = pd.read_csv('https://archive.ics.uci.edu/ml/machine-learning-databases/breast-cancer-wisconsin/breast-cancer-wisconsin.data', header=None, names=names)
# data = load_breast_cancer()

## Definition of Features
Taken from UCI Machine Learning Repository: https://archive.ics.uci.edu/ml/datasets/Breast+Cancer+Wisconsin+%28Original%29

---

**Attribute Information:**

1. Sample code number: id number
2. Clump Thickness: 1 - 10
3. Uniformity of Cell Size: 1 - 10
4. Uniformity of Cell Shape: 1 - 10
5. Marginal Adhesion: 1 - 10
6. Single Epithelial Cell Size: 1 - 10
7. Bare Nuclei: 1 - 10
8. Bland Chromatin: 1 - 10
9. Normal Nucleoli: 1 - 10
10. Mitoses: 1 - 10
11. Class: (2 for benign, 4 for malignant)



In [3]:
df.head()

Sample code number  Clump Thickness  ...  Mitoses  Class
0             1000025                5  ...        1      2
1             1002945                5  ...        1      2
2             1015425                3  ...        1      2
3             1016277                6  ...        1      2
4             1017023                4  ...        1      2

[5 rows x 11 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 699 entries, 0 to 698
Data columns (total 11 columns):
Sample code number             699 non-null int64
Clump Thickness                699 non-null int64
Uniformity of Cell Size        699 non-null int64
Uniformity of Cell Shape       699 non-null int64
Marginal Adhesion              699 non-null int64
Single Epithelial Cell Size    699 non-null int64
Bare Nuclei                    699 non-null object
Bland Chromatin                699 non-null int64
Normal Nucleoli                699 non-null int64
Mitoses                        699 non-null int64
Class                          699 non-null int64
dtypes: int64(10), object(1)
memory usage: 60.2+ KB


In [5]:
print('Ukuran Dataset: ', df.shape)
n_data = df.shape[0]

Ukuran Dataset:  (699, 11)


In [6]:
df = df.iloc[:, 1:]
df['Class'] = df['Class'].map({2:'Benign', 4:'Malignant'})

## Missing Value Detection

In [7]:
miss_data = df[df['Bare Nuclei'] == '?']

In [8]:
miss_data['Class'].iplot(kind='hist', title='Missing Data')

In [9]:
df = df[df['Bare Nuclei'] != '?']

## Distribution of Data

In [10]:
df.iplot(kind='hist', subplots=True, title='Distribution of Data')

## Outlier Detection

In [11]:
df.iplot(kind='box', title='Outlier Detection')

## Feature Selection

## Split the Data

In [12]:
x_train, x_test, y_train, y_test = train_test_split(df.iloc[:, :-1], df.iloc[:, -1], test_size=(100/n_data), stratify=df.iloc[:, -1])
train = pd.DataFrame(x_train, columns=df.columns[:-1])
train['Class'] = y_train
test = pd.DataFrame(x_test, columns=df.columns[:-1])
test['Class'] = y_test

In [13]:
train.head()

Clump Thickness  Uniformity of Cell Size  ...  Mitoses      Class
72                 1                        3  ...        1     Benign
591                2                        5  ...        1  Malignant
487               10                       10  ...        5  Malignant
91                 3                        1  ...        1     Benign
364                2                        1  ...        1     Benign

[5 rows x 10 columns]

In [14]:
train['Class'].value_counts()

Benign       380
Malignant    205
Name: Class, dtype: int64

In [15]:
test.head()

Clump Thickness  Uniformity of Cell Size  ...  Mitoses      Class
694                3                        1  ...        1     Benign
42                 6                       10  ...        3  Malignant
203                5                        1  ...        1     Benign
266               10                       10  ...        2  Malignant
101                2                        3  ...        1  Malignant

[5 rows x 10 columns]

In [16]:
test['Class'].value_counts()

Benign       64
Malignant    34
Name: Class, dtype: int64

In [17]:
# Ukuran Data Training & Testing
print('Ukuran data train:', train.shape)
print('Ukuran data test:', test.shape)

Ukuran data train: (585, 10)
Ukuran data test: (98, 10)


## Build the Model

### Vanilla MLP

In [18]:
mlp = MLPClassifier(hidden_layer_sizes=(11,), solver='sgd')
mlp.fit(train.iloc[:, :-1], train.iloc[:, -1])

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(11,), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=None, shuffle=True, solver='sgd', tol=0.0001,
              validation_fraction=0.1, verbose=False, warm_start=False)

In [19]:
mlp.predict(test.iloc[:, :-1])

array(['Benign', 'Malignant', 'Benign', 'Malignant', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Benign', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Malignant', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Malignant', 'Benign', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Benign', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Benign', 'Benign',
       'Malignant', 'Benign', 'Benign', 'Malignant', 'Malignant',
       'Benign', 'Malignant', 'Benign', 'Benign', 'Malignant',
       'Malignant', 'Benign', 'Benign', 'Benign', 'Benign', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Malignant', 'Benign',
       'Benign', 'Malignant', 'Malignant', 'Benign', 'Malignant',
       'Malignant', 'Benign', 'Malignant', 'Benign', 'Malignant',
       'Benign', 'Malignant', 'Benign', 'Benign', 'Benign', 'Malignant',
       'Benign', 'Benign', 'Benign', 'Benign', 'Benign', 'Benign',
       'Benign', 'Benign', 'Benign', 

In [20]:
mlp.score(test.iloc[:, :-1], test.iloc[:, -1])

0.9081632653061225

### Genetic Algorithm

In [21]:
class GeneticAlgorithm:

    def __init__(self, layer, lowerbound=-0.5, upperbound=0.5, pop_size=10):
        """Inisialisasi class (constructor)
    
        Keyword Arguments:
            layer {tuple} -- jumlah neuron pada masing-masing layer
            lowerbound {float} -- nilai batas bawah untuk inisialisasi bobot dan bias (default: {-0.5})
            upperbound {float} -- nilai batas atas untuk inisialisasi bobot dan bias (default: {0.5})
            pop_size {int} -- jumlah populasi (default: {10})
        """

        self.input = layer[0]
        self.hidden = layer[1]
        self.output = layer[-1]
        self.lowerbound = lowerbound
        self.upperbound = upperbound
        self.pop_size = pop_size

        # Menghitung panjang chromosome
        self.weight_length = (self.input * self.hidden) + (self.hidden * self.output)
        self.bias_length = self.hidden + self.output
        self.chromosome_length = self.weight_length + self.bias_length

    def createPopulation(self):
        # Membuat chromosome
        chromosome = np.random.uniform(self.lowerbound, self.upperbound, (self.pop_size, self.chromosome_length))
        chromosome = pd.DataFrame(chromosome)

        # Membuat dataframe populasi
        population = pd.DataFrame(chromosome)
        population.columns = pd.MultiIndex.from_product([['chromosome'], population.columns])

        return population

    def selectParents(self, population, num_parents):
        parents_idx = np.random.choice(population.shape[0], size=num_parents, replace=False)
        parents = population.iloc[parents_idx].copy()
        return parents

    def crossover(self, population, method='one-cut-point', crossover_rate=0.5):
        # Offspring size = jumlah anak yang akan dihasilkan
        offspring_size = round(crossover_rate * self.pop_size)
        # Memilih induk
        mating_pool = self.selectParents(population, offspring_size)
        mating_pool_copy = mating_pool.copy()
        # Offspring = tempat untuk menampung anak
        offspring = mating_pool.copy()

        # Crossover process
        while(mating_pool_copy.shape[0] != 0):
          if offspring_size % 2 == 0:
            parents = self.selectParents(mating_pool_copy, 2)

            if method == 'extended intermediate':
              # Referensi : (Muhlenbein & Schlierkamp-Voosen, 1993)
              randomNumber = np.random.uniform(-0.25, 1.25, parents['chromosome'].shape[1])
              offspring['chromosome'].loc[parents.index[0]] = parents['chromosome'].iloc[0] + randomNumber * (parents['chromosome'].iloc[1] - parents['chromosome'].iloc[0])
              offspring['chromosome'].loc[parents.index[1]] = parents['chromosome'].iloc[1] + randomNumber * (parents['chromosome'].iloc[0] - parents['chromosome'].iloc[1])
            else:
              # One-cut-point crossover
              cut_point = np.random.choice(parents['chromosome'].shape[1])
              offspring['chromosome'].loc[parents.index[0]][cut_point:] = parents['chromosome'].iloc[1][cut_point:]
              offspring['chromosome'].loc[parents.index[1]][cut_point:] = parents['chromosome'].iloc[0][cut_point:]

            mating_pool_copy.drop(parents.index, inplace=True)
          else:
            offspring_size += 1
            mating_pool_copy = self.selectParents(population, offspring_size)
        
        return (mating_pool, offspring)

    def mutation(self, population, mutation_rate=0.2):
        # Offspring size = jumlah anak yang akan dihasilkan
        offspring_size = round(mutation_rate * self.pop_size)
        # Memilih induk
        mutation_parents = self.selectParents(population, offspring_size)
        mutation_parents_copy = mutation_parents.copy()
        # Offspring = tempat untuk menampung anak
        offspring = mutation_parents.copy()

        # Mutation process
        while(mutation_parents_copy.shape[0] != 0):
          parents = self.selectParents(mutation_parents_copy, 1)

          mutate_point = np.random.choice(parents['chromosome'].shape[1])
          randomNumber = np.random.uniform(-0.1, 0.1)
          mutated_gene = parents['chromosome', mutate_point].iloc[0] - randomNumber * (self.upperbound - self.lowerbound)
          offspring['chromosome', mutate_point].loc[parents.index[0]] = mutated_gene

          mutation_parents_copy.drop(parents.index, inplace=True)

        return (mutation_parents, offspring)

    def calculateFitness(self, population, train, test):
        fitness = []
        for i in range(population.shape[0]):
          individu = population.iloc[i]
          
          # Weight reshape
          weight = individu['chromosome'][:self.weight_length]
          input_hidden = self.input * self.hidden
          weight_hidden = np.array(weight[:input_hidden]).reshape(self.input, self.hidden)
          weight_output = np.array(weight[input_hidden:]).reshape(self.hidden, self.output)
          weight = [weight_hidden, weight_output]
          
          # Bias reshape
          bias = individu['chromosome'][self.weight_length:]
          bias_hidden = bias[:self.hidden]
          bias_output = bias[self.hidden:]
          bias = [bias_hidden, bias_output]

          # Menghitung fitness
          mlp = MLPClassifier(hidden_layer_sizes=self.hidden, solver='sgd')
          mlp.fit(train.iloc[:, :-1], train.iloc[:, -1])
          mlp.coefs_ = weight
          mlp.intercepts_ = bias
          accuracy = mlp.score(test.iloc[:, :-1], test.iloc[:, -1])
          fitness.append(accuracy)

        population['fitness'] = fitness
        return population

    def selection(self, population, method='elitism'):
        if method == 'roulette wheel':
          population_copy = population.copy()
          # Probabilitas individu akan terpilih
          population_copy['prob'] = population_copy['fitness'] / population_copy['fitness'].sum()
          # Probabilitas kumulatif
          population_copy['probCum'] = population_copy['prob'].cumsum()
          
          random_number = np.random.rand(self.pop_size)
          roulette_selection =[population_copy[r < population_copy['probCum']].index[0] for r in random_number]

          population = population.loc[roulette_selection]
        elif method == 'binary tournament':
          # Mengambil secara acak
          individu = np.random.choice(population.shape[0], (self.pop_size, 2))

          # Mengambil nilai fitness masing-masing kandidat biner
          fitness1 = population.loc[individu[:, 0], 'fitness']
          fitness2 = population.loc[individu[:, 1], 'fitness']

          # Proses seleksi
          binary_selection = np.argmax([fitness1, fitness2], axis=0)
          filter1 = np.argwhere(binary_selection == 0).flatten()
          filter2 = np.argwhere(binary_selection == 1).flatten()
          individu1 = fitness1.iloc[filter1]
          individu2 = fitness2.iloc[filter2]
          individu_selection = pd.concat([individu1, individu2])
          
          population = population.loc[individu_selection.index]
        else:
          population = population.nlargest(self.pop_size, 'fitness')
        
        population = population.reset_index(drop=True)
        return population

    def optimize(self, generation, train, test, crossover_rate=0.4, mutation_rate=0.2, crossover_method='one-cut-point', selection_method='elitism'):
        # Jumlah individu dalam satu populasi
        population = self.createPopulation()
        
        for gen in range(generation):
          # Crossover
          parents_crossover, offspring_crossover = self.crossover(population, method=crossover_method, crossover_rate=crossover_rate)

          # Mutation
          parents_mutation, offspring_mutation = self.mutation(population, mutation_rate=mutation_rate)

          # Offspring
          offspring = pd.concat([offspring_crossover, offspring_mutation], ignore_index=True)

          # Populasi baru
          population = pd.concat([population, offspring], ignore_index=True)

          # Menghitung nilai fitness
          population = self.calculateFitness(population, train, test)

          # Seleksi
          population = self.selection(population, selection_method)

        return population

    def visualize(self, generation, train, test, crossover_rate=0.4, mutation_rate=0.2, crossover_method='one-cut-point', selection_method='elitism'):
        # Jumlah generasi yang akan dievaluasi
        generation_eval = np.arange(1, generation)
        # Fungsi fitness
        fitness_best = []
        fitness_average = []

        for gen in generation_eval:
          population = self.optimize(gen, train, test, crossover_rate, mutation_rate, crossover_method, selection_method)
          best = population['fitness'].max()
          average = population['fitness'].mean()
          fitness_best.append(best)
          fitness_average.append(average)

        # Visualisasi
        trace_best = go.Scatter(x=generation_eval, y=fitness_best, mode='lines+markers', name='Terbaik')
        trace_average = go.Scatter(x=generation_eval, y=fitness_average, mode='lines+markers', name='Rata-Rata')
        fig = go.Figure(data=[trace_best, trace_average])
        fig.update_layout(title_text='Hasil Optimasi', xaxis_title='Generasi', yaxis_title='Fitness')
        fig.show()

In [22]:
layer = (df.shape[1]-1, 11, 1)
lowerbound = -0.5
upperbound = 0.5
ga = GeneticAlgorithm(layer, lowerbound, upperbound, pop_size=10)

#### Initialization

In [23]:
population = ga.createPopulation()
population

chromosome                      ...                              
         0         1         2    ...       119       120       121
0   0.054563 -0.073248 -0.205144  ... -0.104915 -0.094724 -0.257863
1   0.243723 -0.169506  0.430190  ... -0.242119 -0.246629  0.328486
2   0.390485  0.463495 -0.036469  ... -0.025356 -0.084285  0.264149
3  -0.336738 -0.359456  0.356071  ... -0.040255  0.441847  0.475761
4   0.136486 -0.040925 -0.042634  ...  0.036767  0.316553 -0.450586
5   0.076067 -0.208841  0.389523  ... -0.371903  0.259759 -0.086464
6  -0.330070 -0.476408  0.358021  ... -0.387610  0.297654  0.062564
7   0.174661 -0.346022 -0.419102  ... -0.110457 -0.093561 -0.105082
8  -0.178397  0.334204  0.327177  ...  0.082815  0.043708 -0.185474
9  -0.139859 -0.418487 -0.395717  ... -0.086514 -0.042930  0.227900

[10 rows x 122 columns]

#### Reproduction

In [24]:
parents_crossover, offspring_crossover = ga.crossover(population, method='extended intermediate', crossover_rate=0.4)

In [25]:
parents_crossover

chromosome                      ...                              
         0         1         2    ...       119       120       121
4   0.136486 -0.040925 -0.042634  ...  0.036767  0.316553 -0.450586
7   0.174661 -0.346022 -0.419102  ... -0.110457 -0.093561 -0.105082
1   0.243723 -0.169506  0.430190  ... -0.242119 -0.246629  0.328486
2   0.390485  0.463495 -0.036469  ... -0.025356 -0.084285  0.264149

[4 rows x 122 columns]

In [26]:
offspring_crossover

chromosome                      ...                              
         0         1         2    ...       119       120       121
4   0.193511 -0.109863  0.082643  ...  0.013505 -0.230576 -0.441428
7   0.310136  0.014923 -0.421400  ... -0.046928 -0.083555  0.180653
1   0.186699 -0.100568  0.304913  ... -0.218856  0.300500  0.319328
2   0.255010  0.102551 -0.034171  ... -0.088885 -0.094290 -0.021586

[4 rows x 122 columns]

In [27]:
parents_mutation, offspring_mutation = ga.mutation(population, mutation_rate=0.2)

In [28]:
parents_mutation

chromosome                      ...                              
         0         1         2    ...       119       120       121
7   0.174661 -0.346022 -0.419102  ... -0.110457 -0.093561 -0.105082
9  -0.139859 -0.418487 -0.395717  ... -0.086514 -0.042930  0.227900

[2 rows x 122 columns]

In [29]:
offspring_mutation

chromosome                      ...                              
         0         1         2    ...       119       120       121
7   0.174661 -0.346022 -0.419102  ... -0.110457 -0.093561 -0.105082
9  -0.139859 -0.418487 -0.395717  ... -0.086514 -0.042930  0.227900

[2 rows x 122 columns]

In [30]:
offspring = pd.concat([offspring_crossover, offspring_mutation], ignore_index=True)
offspring

chromosome                      ...                              
         0         1         2    ...       119       120       121
0   0.193511 -0.109863  0.082643  ...  0.013505 -0.230576 -0.441428
1   0.310136  0.014923 -0.421400  ... -0.046928 -0.083555  0.180653
2   0.186699 -0.100568  0.304913  ... -0.218856  0.300500  0.319328
3   0.255010  0.102551 -0.034171  ... -0.088885 -0.094290 -0.021586
4   0.174661 -0.346022 -0.419102  ... -0.110457 -0.093561 -0.105082
5  -0.139859 -0.418487 -0.395717  ... -0.086514 -0.042930  0.227900

[6 rows x 122 columns]

#### Calculate Fitness

In [31]:
# Populasi baru
population = pd.concat([population, offspring], ignore_index=True)

# Menghitung fungsi fitness
population = ga.calculateFitness(population, train, test)

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iteration

In [32]:
population

chromosome                      ...                       fitness
            0         1         2  ...       120       121          
0    0.054563 -0.073248 -0.205144  ... -0.094724 -0.257863  0.377551
1    0.243723 -0.169506  0.430190  ... -0.246629  0.328486  0.642857
2    0.390485  0.463495 -0.036469  ... -0.084285  0.264149  0.622449
3   -0.336738 -0.359456  0.356071  ...  0.441847  0.475761  0.357143
4    0.136486 -0.040925 -0.042634  ...  0.316553 -0.450586  0.357143
5    0.076067 -0.208841  0.389523  ...  0.259759 -0.086464  0.520408
6   -0.330070 -0.476408  0.358021  ...  0.297654  0.062564  0.459184
7    0.174661 -0.346022 -0.419102  ... -0.093561 -0.105082  0.346939
8   -0.178397  0.334204  0.327177  ...  0.043708 -0.185474  0.367347
9   -0.139859 -0.418487 -0.395717  ... -0.042930  0.227900  0.346939
10   0.193511 -0.109863  0.082643  ... -0.230576 -0.441428  0.459184
11   0.310136  0.014923 -0.421400  ... -0.083555  0.180653  0.581633
12   0.186699 -0.100568  0.304913  ...  0.300500  0.319328  0.357143
13   0.255010  0.102551 -0.034171  ... -0.094290 -0.021586  0.438776
14   0.174661 -0.346022 -0.419102  ... -0.093561 -0.105082  0.346939
15  -0.139859 -0.418487 -0.395717  ... -0.042930  0.227900  0.346939

[16 rows x 123 columns]

#### Selection

In [33]:
population = ga.selection(population, 'binary tournament')
population

chromosome                      ...                       fitness
           0         1         2  ...       120       121          
0   0.076067 -0.208841  0.389523  ...  0.259759 -0.086464  0.520408
1   0.390485  0.463495 -0.036469  ... -0.084285  0.264149  0.622449
2   0.243723 -0.169506  0.430190  ... -0.246629  0.328486  0.642857
3   0.193511 -0.109863  0.082643  ... -0.230576 -0.441428  0.459184
4   0.136486 -0.040925 -0.042634  ...  0.316553 -0.450586  0.357143
5   0.243723 -0.169506  0.430190  ... -0.246629  0.328486  0.642857
6   0.390485  0.463495 -0.036469  ... -0.084285  0.264149  0.622449
7  -0.330070 -0.476408  0.358021  ...  0.297654  0.062564  0.459184
8  -0.330070 -0.476408  0.358021  ...  0.297654  0.062564  0.459184
9   0.390485  0.463495 -0.036469  ... -0.084285  0.264149  0.622449

[10 rows x 123 columns]

#### Visualization

In [34]:
ga.visualize(20, train, test, crossover_method='extended intermediate', selection_method='binary tournament')

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iteration

### Genetic MLP

In [35]:
population = ga.optimize(20, train, test, crossover_method='extended intermediate', selection_method='binary tournament')
population

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iteration

chromosome                      ...                       fitness
           0         1         2  ...       120       121          
0  -0.224832 -0.485319  0.084984  ... -0.381077 -0.452785  0.867347
1  -0.224832 -0.485319  0.130040  ... -0.381077 -0.452785  0.867347
2  -0.224832 -0.485319  0.084984  ... -0.381077 -0.452785  0.867347
3  -0.224832 -0.485319  0.130040  ... -0.381077 -0.452785  0.867347
4  -0.224832 -0.485319  0.085468  ... -0.381077 -0.452785  0.867347
5  -0.224832 -0.485319  0.130040  ... -0.381077 -0.452785  0.867347
6  -0.224832 -0.485319  0.085468  ... -0.381077 -0.452785  0.867347
7  -0.224832 -0.485319  0.085031  ... -0.381077 -0.452785  0.867347
8  -0.224832 -0.485319  0.084984  ... -0.381077 -0.452785  0.867347
9  -0.224832 -0.485319  0.130040  ... -0.381077 -0.452785  0.867347

[10 rows x 123 columns]

In [36]:
individu = population.iloc[0]
          
# Weight reshape
weight = individu['chromosome'][:ga.weight_length]
input_hidden = ga.input * ga.hidden
weight_hidden = np.array(weight[:input_hidden]).reshape(ga.input, ga.hidden)
weight_output = np.array(weight[input_hidden:]).reshape(ga.hidden, ga.output)
weight = [weight_hidden, weight_output]
          
# Bias reshape
bias = individu['chromosome'][ga.weight_length:]
bias_hidden = bias[:ga.hidden]
bias_output = bias[ga.hidden:]
bias = [bias_hidden, bias_output]

# Menghitung fitness
mlp = MLPClassifier(hidden_layer_sizes=ga.hidden, solver='sgd')
mlp.fit(train.iloc[:, :-1], train.iloc[:, -1])
mlp.coefs_ = weight
mlp.intercepts_ = bias

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



In [37]:
actual = test.iloc[:, -1]
pred = mlp.predict(test.iloc[:, :-1])

## Evaluation

### Confusion Matrix

In [53]:
cm = confusion_matrix(actual, pred)
x = ['True', 'False']
y = ['Positive', 'Negative']

hm = go.Heatmap(z=cm.T, x=x, y=y, colorscale='Blues')
layout = go.Layout(title='Confusion Matrix', xaxis_title='Actual Class', yaxis_title='Predicted Class', yaxis=dict(autorange='reversed'))
fig = go.Figure(data=hm, layout=layout)
fig.show()

### Classification Report

In [56]:
print(classification_report(actual, pred))

              precision    recall  f1-score   support

      Benign       0.84      0.98      0.91        64
   Malignant       0.96      0.65      0.77        34

    accuracy                           0.87        98
   macro avg       0.90      0.82      0.84        98
weighted avg       0.88      0.87      0.86        98



## Cross Validation

In [59]:
skf = StratifiedKFold(n_splits=10)
skf.get_n_splits(df.iloc[:, :-1], df.iloc[:, -1])

10

### Vanilla MLP

In [64]:
mlp = MLPClassifier(hidden_layer_sizes=(11,), solver='sgd')

i = 1
for train_index, test_index in skf.split(df.iloc[:, :-1], df.iloc[:, -1]):
  print('Fold ', i)
  # print("TRAIN:", train_index, "TEST:", test_index)
  mlp.fit(df.iloc[train_index, :-1], df.iloc[train_index, -1])
  print('Score: ', mlp.score(df.iloc[test_index, :-1], df.iloc[test_index, -1]))
  i += 1

Fold  1


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.8695652173913043
Fold  2


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.8695652173913043
Fold  3


...

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.9705882352941176
Fold  9


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.9852941176470589
Fold  10
Score:  0.9850746268656716


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



### Genetic MLP

In [65]:
mlp = MLPClassifier(hidden_layer_sizes=ga.hidden, solver='sgd')

i = 1
for train_index, test_index in skf.split(df.iloc[:, :-1], df.iloc[:, -1]):
  print('Fold ', i)
  # print("TRAIN:", train_index, "TEST:", test_index)
  mlp.fit(df.iloc[train_index, :-1], df.iloc[train_index, -1])
  mlp.coefs_ = weight
  mlp.intercepts_ = bias
  print('Score: ', mlp.score(df.iloc[test_index, :-1], df.iloc[test_index, -1]))
  i += 1

Fold  1


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.7536231884057971
Fold  2


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.7536231884057971
Fold  3


...

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.8676470588235294
Fold  9


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



Score:  0.8970588235294118
Fold  10
Score:  0.9402985074626866


/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/multilayer_perceptron.py:566: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.



## Conclusion